In [36]:
import numpy as np
import requests
import pandas as pd
import folium
df_train = pd.read_csv('nyc_taxi/train.csv').drop(columns=['trip_duration', 'dropoff_datetime'])
df_test = pd.read_csv('nyc_taxi/test.csv')
df = pd.concat([df_train, df_test], sort=False, ignore_index=True)
df.pickup_datetime = pd.to_datetime(df.pickup_datetime, format='%Y-%m-%d %H:%M:%S')
df['month'] = df.pickup_datetime.apply(lambda x: x.month)
df['week'] = df.pickup_datetime.apply(lambda x: x.week)
df['day'] = df.pickup_datetime.apply(lambda x: x.day)
df['hour'] = df.pickup_datetime.apply(lambda x: x.hour)

In [56]:
from jupyterthemes import jtplot
jtplot.style()

In [37]:
df.head()

id  vendor_id     pickup_datetime  passenger_count  \
0  id2875421          2 2016-03-14 17:24:55                1   
1  id2377394          1 2016-06-12 00:43:35                1   
2  id3858529          2 2016-01-19 11:35:24                1   
3  id3504673          2 2016-04-06 19:32:31                1   
4  id2181028          2 2016-03-26 13:30:55                1   

   pickup_longitude  pickup_latitude  dropoff_longitude  dropoff_latitude  \
0        -73.982155        40.767937         -73.964630         40.765602   
1        -73.980415        40.738564         -73.999481         40.731152   
2        -73.979027        40.763939         -74.005333         40.710087   
3        -74.010040        40.719971         -74.012268         40.706718   
4        -73.973053        40.793209         -73.972923         40.782520   

  store_and_fwd_flag  month  week  day  hour  
0                  N      3    11   14    17  
1                  N      6    23   12     0  
2                  N      1     3   19    11  
3                  N      4    14    6    19  
4                  N      3    12   26    13

In [60]:
def generateBaseMap(default_location=[40.693943, -73.985880], default_zoom_start=12):
    base_map = folium.Map(location=default_location, control_scale=True, zoom_start=default_zoom_start)
    return base_map

In [61]:
base_map = generateBaseMap()

In [81]:
from folium.plugins import HeatMap
df_copy = df[df.month>4].copy()
df_copy['count'] = 1
# HeatMap(data=df_copy[['pickup_latitude', 'pickup_longitude', 'count']].groupby(['pickup_latitude', 'pickup_longitude']).sum().reset_index().values.tolist(), radius=8, max_zoom=13).add_to(base_map)
# base_map.add_child(folium.ClickForMarker(popup='Potential Location'))
df_hour_list = []
for hour in df_copy.hour.sort_values().unique():
    df_hour_list.append(df_copy.loc[df_copy.hour == hour, ['pickup_latitude', 'pickup_longitude', 'count']].groupby(['pickup_latitude', 'pickup_longitude']).sum().reset_index().sample(5000).values.tolist())

In [82]:
from folium.plugins import HeatMapWithTime
base_map = generateBaseMap(default_zoom_start=15)
HeatMapWithTime(df_hour_list, radius=5, gradient={0.2: 'blue', 0.4: 'lime', 0.6: 'orange', 1: 'red'}, min_opacity=0.5, max_opacity=0.8, use_local_extrema=True).add_to(base_map)
base_map

## Weather API

In [19]:
with open('apikey.txt', 'rt') as fp:
    API_KEY = fp.read()
CITY_ID = 1277333

In [34]:
URL = 'http://maps.openweathermap.org/maps/2.0/weather/{op}/{z}/{x}/{y}?appid={appid}'.format(op='TA2',z=11, x=77.6271, y=12.9279, appid=API_KEY)
print(URL)
response = requests.get(URL)

http://maps.openweathermap.org/maps/2.0/weather/TA2/11/77.6271/12.9279?appid=ff8c00e9c4c48c4c5a5021c6671c27ee



In [33]:
print(response.content)

b'{"cod":401, "message": "Invalid API key. Please see http://openweathermap.org/faq#error401 for more info."}'
